In [1]:
# test probe loading 
import pickle as pkl
import numpy as np
import sklearn 
from sklearn import linear_model
import os
os.environ["PYTORCH_ENABLE_MPS_FALLBACK"] = "1"

# load the probe data
with open("./model/20240625-131035_demo.pkl", "rb") as f:
    probe_data = pkl.load(f)
# take the NQ open one
probe_data = probe_data[-2]
probe_data

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


/Users/shreshth/anaconda3/envs/llm-test/lib/python3.11/site-packages/threadpoolctl.py:1214: RuntimeWarning: 
Found Intel OpenMP ('libiomp') and LLVM OpenMP ('libomp') loaded at
the same time. Both libraries are known to be incompatible and this
can cause random crashes or deadlocks on Linux when loaded in the
same Python program.
Using threadpoolctl may cause crashes or deadlocks. For more
information and possible workarounds, please see
    https://github.com/joblib/threadpoolctl/blob/master/multiple_openmp.md

  warnings.warn(msg, RuntimeWarning)


{'name': 'nq',
 't_bmodel': LogisticRegression(),
 't_amodel': LogisticRegression(),
 'sep_layer_range': (27, 32),
 'ap_layer_range': (17, 22)}

In [2]:
probe = probe_data['t_bmodel']
layer_range = probe_data['sep_layer_range']

In [5]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer, TextIteratorStreamer

model_id = "meta-llama/Llama-2-7b-chat-hf"
model = AutoModelForCausalLM.from_pretrained(model_id, device_map="cpu")
tokenizer = AutoTokenizer.from_pretrained(model_id)
tokenizer.use_default_system_prompt = False

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [8]:
from threading import Thread

system_prompt = "You are a helpful assistant."
message = "what is the capital of France?"
max_new_tokens = 100
top_p = 0.9
top_k = 50
temperature = 0.7
repetition_penalty = 1.2

conversation = []

conversation.append({"role": "system", "content": system_prompt})
conversation.append({"role": "user", "content": message})
input_ids = tokenizer.apply_chat_template(conversation, return_tensors="pt")
input_ids = input_ids.to(model.device)
print(input_ids, input_ids.shape)
streamer = TextIteratorStreamer(tokenizer, timeout=1000.0, skip_prompt=True, skip_special_tokens=True)
generation_kwargs = dict(
    input_ids=input_ids,
    max_new_tokens=max_new_tokens,
    do_sample=True,
    top_p=top_p,
    top_k=top_k,
    temperature=temperature,
    repetition_penalty=repetition_penalty,
    streamer=streamer,
    output_hidden_states=True,
    return_dict_in_generate=True,
)

thread = Thread(target=model.generate, kwargs=generation_kwargs)
thread.start()

generated_text = ""
highlighted_text = ""

for new_text in streamer:
    print(new_text)
    generated_text += new_text
    current_input_ids = tokenizer.encode(generated_text, return_tensors="pt").to(model.device)
    print(current_input_ids, current_input_ids.shape)
    with torch.no_grad():
        outputs = model(current_input_ids, output_hidden_states=True)
        print(outputs)
        hidden = outputs.hidden_states    
        print(hidden.shape)
        # Stack second last token embeddings from all layers 
        # if len(hidden) == 1:  # FIX: runtime error for mistral-7b on bioasq
        #     sec_last_input = hidden[0]
        # elif ((n_generated - 2) >= len(hidden)):
        #     sec_last_input = hidden[-2]
        # else:
        #     sec_last_input = hidden[n_generated - 2]
        # sec_last_token_embedding = torch.stack([layer[:, -1, :].cpu() for layer in sec_last_input])
        # print(sec_last_token_embedding.shape)
    last_hidden_state = outputs.hidden_states[-1][:, -1, :].cpu().numpy()
    print(last_hidden_state.shape)  
    # TODO potentially need to only compute uncertainty for the last token in sentence?


tensor([[    1,   518, 25580, 29962,  3532, 14816, 29903,  6778,    13,  3492,
           526,   263,  8444, 20255, 29889,    13, 29966,   829, 14816, 29903,
          6778,    13,    13,  5816,   338,   278,  7483,   310,  3444, 29973,
           518, 29914, 25580, 29962]]) torch.Size([1, 34])


We detected that you are passing `past_key_values` as a tuple and this is deprecated and will be removed in v4.43. Please use an appropriate `Cache` class (https://huggingface.co/docs/transformers/v4.41.3/en/internal/generation_utils#transformers.Cache)


In [ ]:
# concat hidden states


hidden_states = np.concatenate(np.array(hidden_states)[layer_range], axis=1)
# predict with probe
pred = probe.predict(hidden_states)
print(pred)